# Generating Bach Music Project

### Dependencies

In [1]:
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow import keras
import os
from IPython.display import Image

### Filepaths

In [2]:
filepath = "C:/Users/VTSB/Desktop/CS Resources/AI Hands-On ML/datasets/bach"

train_root_filepath = filepath + "/" + "train"
test_root_filepath = filepath + "/" + "test"
valid_root_filepath = filepath + "/" + "valid"

for train, test, valid in zip(os.walk(train_root_filepath), os.walk(test_root_filepath), os.walk(valid_root_filepath)):
    train_root, train_dirs, train_files = train
    test_root, test_dirs, test_files = test
    valid_root, valid_dirs, valid_files = valid

train_filepaths = [train_root_filepath + "/" + filename for filename in train_files]
test_filepaths = [test_root_filepath + "/" + filename for filename in test_files]
valid_filepaths = [valid_root_filepath + "/" + filename for filename in valid_files]

### Reading the Filepaths

In [3]:
import random

random.seed(10)
def read_dataset(filepaths, shuffle=False):
    if shuffle: filepaths = random.shuffle(filepaths)
    DFs = [pd.read_csv(s).values.astype(np.int32).tolist() for s in filepaths]
    return DFs

train_chorales = read_dataset(train_filepaths)
test_chorales = read_dataset(test_filepaths)
valid_chorales = read_dataset(valid_filepaths)

In [4]:
notes = set()
for chorales in (train_chorales, valid_chorales, test_chorales):
    for chorale in chorales:
        for chord in chorale:
            notes |= set(chord)

n_notes = len(notes)
min_note = min(notes - {0})
max_note = max(notes)

assert min_note == 36
assert max_note == 81

In [5]:
# this block of code is left on hold as I have not learned much about windows yet

def create_target(batch):
    X = batch[:, :-1]
    Y = batch[:, 1:] # predict next note in each arpegio, at each step
    return X, Y

def preprocess(window):
    window = tf.where(window == 0, window, window - min_note + 1) # shift values
    return tf.reshape(window, [-1]) # convert to arpegio

def bach_dataset(chorales, batch_size=32, 
                 window_size=32, window_shift=16, cache=True):
    def batch_window(window):
        return window.batch(window_size + 1)

    def to_windows(chorale):
        dataset = tf.data.Dataset.from_tensor_slices(chorale) # inner dataset with each tensor as a chord
        dataset = dataset.window(window_size + 1, window_shift, drop_remainder=False)
        return dataset # .flat_map(batch_window)

    def to_windows2(chorale):
        dataset = tf.data.Dataset.from_tensor_slices(chorale) 
        dataset = dataset.window(window_size + 1, window_shift, drop_remainder=True)
        return dataset
    
    def to_windows3(chorale):
        dataset = tf.data.Dataset.from_tensor_slices(chorale) 
        dataset = dataset.window(window_size + 1, window_shift, drop_remainder=True)
        return dataset.flat_map(batch_window)
    
    def to_windows1(chorale):
        dataset = tf.data.Dataset.from_tensor_slices(chorale) 
        return dataset
    
    chorales = tf.ragged.constant(chorales, ragged_rank=1) # why is it ragged_rank=1?
    # print(chorales); 1 raggedtensor holding all chorales 
    dataset = tf.data.Dataset.from_tensor_slices(chorales)
    # tensor for every chorale
    dataset0 = dataset.map(to_windows) # dataset of datasets; flattens the inner datasets after the map
    dataset1 = dataset.map(to_windows1)
    dataset2 = dataset.map(to_windows2)
    dataset3 = dataset.map(to_windows3)
    dataset4 = dataset.flat_map(to_windows3)
    dataset5 = dataset4.map(preprocess)


    dataset5 = dataset5.batch(batch_size)
    dataset5 = dataset5.map(create_target)
    return dataset0, dataset1, dataset2, dataset3, dataset4, dataset5

train_set, train_set1, train_set2, train_set3, train_set4, train_set5 = bach_dataset(train_chorales)

In [6]:
def bach_dataset1(chorales, batch_size=32, 
                 window_size=32, window_shift=16, cache=True, rank=1):
    chorales = tf.ragged.constant(chorales, ragged_rank=rank)
    return chorales

train_set_6 = bach_dataset1(train_chorales)
train_set_7 = bach_dataset1(train_chorales, rank=2)
train_set_8 = bach_dataset1(train_chorales, rank=None)

In [7]:
train_set_6.shape, train_set_7.shape, train_set_8.shape

(TensorShape([229, None, 4]),
 TensorShape([229, None, None]),
 TensorShape([229, None, None]))

In [8]:
train_set_6

<tf.RaggedTensor [[[74, 70, 65, 58], [74, 70, 65, 58], [74, 70, 65, 58], [74, 70, 65, 58], [75, 70, 58, 55], [75, 70, 58, 55], [75, 70, 60, 55], [75, 70, 60, 55], [77, 69, 62, 50], [77, 69, 62, 50], [77, 69, 62, 50], [77, 69, 62, 50], [77, 70, 62, 55], [77, 70, 62, 55], [77, 69, 62, 55], [77, 69, 62, 55], [75, 67, 63, 48], [75, 67, 63, 48], [75, 69, 63, 48], [75, 69, 63, 48], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [75, 69, 63, 48], [75, 69, 63, 48], [75, 67, 63, 48], [75, 67, 63, 48], [77, 65, 62, 50], [77, 65, 62, 50], [77, 65, 60, 50], [77, 65, 60, 50], [74, 67, 58, 55], [74, 67, 58, 55], [74, 67, 58, 53], [74, 67, 58, 53], [72, 67, 58, 51], [72, 67, 58, 51], [72, 67, 58, 51], [72, 67, 58, 51], [72, 65, 57, 53], [72, 65, 57, 53], [72, 65, 

In [9]:
train_set_7

<tf.RaggedTensor [[[74, 70, 65, 58], [74, 70, 65, 58], [74, 70, 65, 58], [74, 70, 65, 58], [75, 70, 58, 55], [75, 70, 58, 55], [75, 70, 60, 55], [75, 70, 60, 55], [77, 69, 62, 50], [77, 69, 62, 50], [77, 69, 62, 50], [77, 69, 62, 50], [77, 70, 62, 55], [77, 70, 62, 55], [77, 69, 62, 55], [77, 69, 62, 55], [75, 67, 63, 48], [75, 67, 63, 48], [75, 69, 63, 48], [75, 69, 63, 48], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [75, 69, 63, 48], [75, 69, 63, 48], [75, 67, 63, 48], [75, 67, 63, 48], [77, 65, 62, 50], [77, 65, 62, 50], [77, 65, 60, 50], [77, 65, 60, 50], [74, 67, 58, 55], [74, 67, 58, 55], [74, 67, 58, 53], [74, 67, 58, 53], [72, 67, 58, 51], [72, 67, 58, 51], [72, 67, 58, 51], [72, 67, 58, 51], [72, 65, 57, 53], [72, 65, 57, 53], [72, 65, 

In [10]:
train_set_8

<tf.RaggedTensor [[[74, 70, 65, 58], [74, 70, 65, 58], [74, 70, 65, 58], [74, 70, 65, 58], [75, 70, 58, 55], [75, 70, 58, 55], [75, 70, 60, 55], [75, 70, 60, 55], [77, 69, 62, 50], [77, 69, 62, 50], [77, 69, 62, 50], [77, 69, 62, 50], [77, 70, 62, 55], [77, 70, 62, 55], [77, 69, 62, 55], [77, 69, 62, 55], [75, 67, 63, 48], [75, 67, 63, 48], [75, 69, 63, 48], [75, 69, 63, 48], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [72, 69, 65, 53], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [74, 70, 65, 46], [75, 69, 63, 48], [75, 69, 63, 48], [75, 67, 63, 48], [75, 67, 63, 48], [77, 65, 62, 50], [77, 65, 62, 50], [77, 65, 60, 50], [77, 65, 60, 50], [74, 67, 58, 55], [74, 67, 58, 55], [74, 67, 58, 53], [74, 67, 58, 53], [72, 67, 58, 51], [72, 67, 58, 51], [72, 67, 58, 51], [72, 67, 58, 51], [72, 65, 57, 53], [72, 65, 57, 53], [72, 65, 

In [11]:
for i, j, z in zip(train_set_6, train_set_7, train_set_8):
    print("I:", i)
    print("J:", j)
    print("Z:", z)

I: tf.Tensor(
[[74 70 65 58]
 [74 70 65 58]
 [74 70 65 58]
 [74 70 65 58]
 [75 70 58 55]
 [75 70 58 55]
 [75 70 60 55]
 [75 70 60 55]
 [77 69 62 50]
 [77 69 62 50]
 [77 69 62 50]
 [77 69 62 50]
 [77 70 62 55]
 [77 70 62 55]
 [77 69 62 55]
 [77 69 62 55]
 [75 67 63 48]
 [75 67 63 48]
 [75 69 63 48]
 [75 69 63 48]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [75 69 63 48]
 [75 69 63 48]
 [75 67 63 48]
 [75 67 63 48]
 [77 65 62 50]
 [77 65 62 50]
 [77 65 60 50]
 [77 65 60 50]
 [74 67 58 55]
 [74 67 58 55]
 [74 67 58 53]
 [74 67 58 53]
 [72 67 58 51]
 [72 67 58 51]
 [72 67 58 51]
 [72 67 58 51]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [72 69 65 53]
 [72 69 65 

 [69 61 52 45]], shape=(212, 4), dtype=int32)
J: <tf.RaggedTensor [[69, 64, 60, 45], [69, 64, 60, 45], [69, 65, 62, 45], [69, 65, 62, 45], [69, 64, 60, 57], [69, 64, 60, 57], [69, 64, 59, 57], [69, 64, 59, 57], [69, 64, 57, 53], [69, 64, 57, 53], [69, 62, 57, 53], [69, 62, 57, 53], [76, 64, 57, 48], [76, 64, 57, 48], [76, 64, 60, 48], [76, 64, 60, 48], [74, 65, 59, 50], [74, 65, 59, 50], [74, 65, 57, 50], [74, 65, 57, 50], [76, 64, 59, 44], [76, 64, 59, 44], [76, 64, 59, 44], [76, 64, 59, 44], [72, 64, 57, 45], [72, 64, 57, 45], [72, 64, 57, 45], [72, 64, 57, 45], [71, 64, 56, 52], [71, 64, 56, 52], [71, 64, 56, 52], [71, 64, 56, 52], [69, 64, 57, 48], [69, 64, 57, 48], [71, 64, 57, 47], [71, 64, 57, 47], [72, 69, 64, 45], [72, 69, 64, 45], [72, 69, 64, 45], [72, 69, 64, 45], [71, 68, 64, 52], [71, 68, 64, 52], [71, 68, 64, 52], [71, 68, 64, 52], [72, 69, 64, 57], [72, 69, 64, 57], [74, 69, 64, 59], [74, 69, 64, 59], [76, 67, 64, 60], [76, 67, 64, 60], [76, 69, 64, 60], [76, 69, 64, 60

I: tf.Tensor(
[[67 62 58 43]
 [67 62 58 43]
 [69 62 60 43]
 [69 62 60 43]
 [70 67 62 55]
 [70 67 62 55]
 [70 65 62 55]
 [70 65 62 55]
 [69 63 60 48]
 [69 63 60 48]
 [67 63 58 48]
 [67 63 58 48]
 [66 62 57 50]
 [66 62 57 50]
 [66 62 57 60]
 [66 62 57 60]
 [67 62 58 58]
 [67 62 58 58]
 [69 66 60 57]
 [69 66 60 57]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 63 48]
 [70 67 63 48]
 [69 66 57 50]
 [69 66 57 50]
 [69 66 62 50]
 [69 66 62 50]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [72 65 60 57]
 [72 65 60 57]
 [72 67 60 57]
 [72 67 60 57]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [74 70 65 58]
 [74 70 65 58]
 [74 70 65 57]
 [74 70 65 57]
 [70 62 67 55]
 [70 62 67 55]
 [70 62 67 53]
 [70 62 67 53]
 [72 67 67 51]
 [72 67 67 51]
 [72 70 67 50]
 [72 70 67 50]
 [72 69 60 51]
 [72 69 60 51]
 [72 67 62 51]
 [72 67 63 51]
 [74 66 57 50]
 [74 66 57 50]
 [74 66 57 50]
 [74 66 57 50]
 [74 67 58 55]
 [74 67 58 

I: tf.Tensor(
[[71 68 64 64]
 [71 68 64 64]
 [71 69 66 64]
 [71 69 66 64]
 [71 68 64 52]
 [71 68 64 52]
 [71 66 63 52]
 [71 66 63 52]
 [73 64 61 57]
 [73 64 61 57]
 [73 64 61 59]
 [73 64 61 59]
 [73 66 63 57]
 [73 66 63 57]
 [73 68 64 56]
 [73 68 64 56]
 [75 69 66 54]
 [75 69 66 54]
 [75 73 69 54]
 [75 73 69 54]
 [75 71 68 47]
 [75 71 68 47]
 [75 69 66 47]
 [75 69 66 47]
 [76 68 64 52]
 [76 68 64 52]
 [76 68 64 52]
 [76 68 64 52]
 [76 68 64 52]
 [76 68 64 52]
 [76 68 64 52]
 [76 68 64 52]
 [78 71 63 59]
 [78 71 63 59]
 [78 71 64 61]
 [78 71 64 61]
 [78 71 66 63]
 [78 71 66 63]
 [78 70 63 59]
 [78 70 63 59]
 [76 68 64 61]
 [76 68 64 61]
 [76 68 63 59]
 [76 68 63 59]
 [76 66 61 58]
 [76 66 61 58]
 [76 66 58 54]
 [76 66 58 54]
 [75 66 59 59]
 [75 66 59 59]
 [75 68 59 56]
 [75 68 59 56]
 [73 68 59 52]
 [73 68 59 52]
 [75 64 59 49]
 [76 64 59 49]
 [73 66 59 54]
 [73 66 59 54]
 [73 66 59 52]
 [73 66 59 52]
 [73 66 58 54]
 [73 66 58 54]
 [73 64 58 54]
 [73 64 58 54]
 [71 63 54 47]
 [71 63 54 

 [67 62 59 43]], shape=(196, 4), dtype=int32)
J: <tf.RaggedTensor [[74, 67, 59, 55], [74, 67, 59, 55], [74, 67, 59, 55], [74, 67, 59, 55], [74, 69, 57, 54], [74, 69, 57, 54], [74, 69, 62, 54], [74, 69, 62, 54], [74, 67, 59, 55], [74, 67, 59, 55], [74, 67, 59, 55], [74, 67, 59, 55], [76, 67, 60, 48], [76, 67, 60, 48], [76, 67, 60, 50], [76, 67, 60, 50], [76, 67, 60, 52], [76, 67, 60, 52], [76, 69, 60, 48], [76, 69, 60, 48], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [74, 71, 62, 55], [71, 67, 62, 55], [71, 67, 62, 55], [71, 67, 62, 55], [71, 67, 62, 55], [72, 69, 62, 55], [72, 69, 62, 55], [72, 69, 62, 54], [72, 69, 62, 54], [71, 62, 62, 55], [71, 62, 62, 55], [71, 62, 67, 55], [71, 62, 67, 55], [69, 62, 66, 50], [69, 62, 66, 50], [69, 62, 66, 48], [69, 62, 66, 48], [71, 62, 67, 47], [71, 62, 67, 47], [72, 62, 55, 52], [72, 62, 55, 52

 [67 62 59 43]], shape=(164, 4), dtype=int32)
J: <tf.RaggedTensor [[67, 62, 59, 55], [67, 62, 59, 55], [67, 62, 59, 55], [67, 62, 59, 55], [74, 62, 57, 54], [74, 62, 57, 54], [74, 64, 57, 54], [74, 64, 57, 54], [74, 66, 57, 50], [74, 66, 57, 50], [74, 66, 59, 50], [74, 66, 60, 50], [74, 67, 59, 55], [74, 67, 59, 55], [74, 67, 57, 57], [74, 67, 57, 57], [74, 67, 55, 59], [74, 67, 55, 59], [74, 65, 55, 55], [74, 65, 55, 55], [76, 64, 55, 60], [76, 64, 55, 60], [76, 67, 55, 60], [76, 67, 55, 60], [74, 66, 62, 62], [74, 66, 62, 62], [72, 66, 62, 62], [72, 66, 62, 62], [71, 67, 62, 55], [71, 67, 62, 55], [71, 67, 62, 55], [71, 67, 62, 55], [69, 69, 62, 54], [69, 69, 62, 54], [69, 69, 62, 54], [69, 69, 62, 54], [71, 67, 55, 52], [71, 67, 55, 52], [73, 67, 55, 52], [73, 67, 55, 52], [74, 66, 62, 59], [74, 66, 62, 59], [74, 66, 61, 57], [74, 66, 61, 57], [74, 64, 59, 55], [74, 64, 59, 55], [74, 64, 64, 55], [74, 64, 64, 55], [73, 64, 69, 57], [73, 64, 69, 57], [73, 64, 67, 57], [73, 64, 67, 57

Z: <tf.RaggedTensor [[71, 64, 56, 50], [71, 64, 56, 50], [71, 64, 56, 50], [71, 64, 56, 50], [71, 64, 56, 50], [71, 64, 56, 50], [71, 64, 56, 50], [71, 64, 56, 50], [64, 64, 57, 48], [64, 64, 57, 48], [64, 64, 57, 48], [64, 64, 57, 48], [71, 68, 62, 47], [71, 68, 62, 47], [71, 68, 62, 47], [71, 68, 62, 47], [72, 69, 64, 45], [72, 69, 64, 45], [72, 69, 64, 45], [72, 69, 64, 45], [71, 67, 62, 47], [71, 67, 62, 47], [69, 66, 62, 47], [69, 66, 62, 47], [67, 64, 64, 48], [67, 64, 64, 48], [67, 64, 62, 47], [67, 64, 62, 47], [69, 66, 60, 45], [69, 66, 60, 45], [69, 66, 60, 45], [69, 66, 60, 45], [71, 68, 59, 52], [71, 68, 59, 52], [71, 68, 59, 52], [71, 68, 59, 52], [71, 68, 59, 52], [71, 68, 59, 52], [71, 68, 59, 52], [71, 68, 59, 52], [71, 68, 64, 52], [71, 68, 64, 52], [71, 68, 64, 52], [71, 68, 64, 52], [71, 68, 64, 52], [71, 68, 64, 52], [71, 68, 64, 52], [71, 68, 64, 52], [72, 69, 64, 57], [72, 69, 64, 57], [72, 69, 64, 57], [72, 69, 64, 57], [74, 71, 65, 55], [74, 71, 65, 55], [74, 71

 [64 59 56 40]], shape=(192, 4), dtype=int32)
J: <tf.RaggedTensor [[64, 59, 55, 52], [64, 59, 55, 52], [64, 59, 55, 52], [64, 59, 55, 52], [71, 59, 54, 52], [71, 59, 54, 52], [71, 59, 54, 50], [71, 59, 54, 50], [71, 64, 55, 48], [71, 64, 55, 48], [71, 63, 55, 48], [71, 63, 55, 48], [69, 64, 54, 48], [69, 64, 54, 48], [69, 64, 52, 48], [69, 64, 52, 48], [71, 63, 54, 47], [71, 63, 54, 47], [71, 63, 54, 57], [71, 63, 54, 57], [64, 64, 59, 55], [64, 64, 59, 55], [66, 63, 57, 54], [66, 63, 57, 54], [67, 64, 59, 52], [67, 64, 59, 52], [67, 64, 59, 50], [67, 64, 59, 50], [67, 64, 64, 48], [67, 64, 64, 48], [67, 64, 62, 47], [67, 64, 62, 47], [67, 64, 61, 46], [67, 64, 61, 46], [67, 64, 61, 46], [67, 64, 61, 46], [66, 64, 54, 47], [66, 64, 54, 47], [66, 63, 59, 47], [66, 63, 57, 47], [64, 59, 55, 40], [64, 59, 55, 40], [64, 59, 55, 40], [64, 59, 55, 40], [64, 59, 55, 40], [64, 59, 55, 40], [64, 59, 55, 40], [64, 59, 55, 40], [67, 64, 59, 52], [67, 64, 59, 52], [67, 64, 59, 50], [67, 64, 59, 50

 [69 64 61 45]], shape=(132, 4), dtype=int32)
J: <tf.RaggedTensor [[69, 64, 61, 45], [69, 64, 61, 45], [69, 64, 62, 47], [69, 64, 62, 47], [69, 64, 64, 49], [69, 64, 64, 49], [69, 62, 64, 47], [69, 62, 64, 47], [69, 61, 64, 45], [69, 61, 64, 45], [69, 59, 64, 45], [69, 59, 64, 45], [66, 57, 62, 50], [66, 57, 62, 50], [66, 57, 62, 49], [66, 57, 62, 49], [71, 66, 63, 47], [71, 66, 63, 47], [71, 68, 63, 47], [71, 68, 63, 47], [69, 68, 64, 49], [69, 68, 64, 49], [69, 66, 64, 49], [69, 64, 64, 49], [69, 66, 59, 51], [69, 66, 59, 51], [69, 66, 59, 51], [69, 66, 59, 51], [68, 64, 59, 52], [68, 64, 59, 52], [68, 64, 59, 52], [68, 64, 59, 52], [73, 64, 57, 57], [73, 64, 57, 57], [73, 64, 57, 57], [73, 64, 57, 57], [73, 69, 64, 57], [73, 69, 64, 57], [73, 69, 64, 56], [73, 69, 64, 56], [73, 69, 66, 54], [73, 69, 66, 54], [73, 69, 66, 52], [73, 69, 66, 52], [78, 69, 59, 51], [78, 69, 59, 51], [78, 69, 59, 51], [78, 69, 59, 51], [76, 68, 59, 52], [76, 68, 59, 52], [76, 68, 59, 54], [76, 68, 59, 54

In [12]:
for i in tf.data.Dataset.from_tensor_slices(train_set_6):
    print(i.shape)
    print(i)

(192, 4)
tf.Tensor(
[[74 70 65 58]
 [74 70 65 58]
 [74 70 65 58]
 [74 70 65 58]
 [75 70 58 55]
 [75 70 58 55]
 [75 70 60 55]
 [75 70 60 55]
 [77 69 62 50]
 [77 69 62 50]
 [77 69 62 50]
 [77 69 62 50]
 [77 70 62 55]
 [77 70 62 55]
 [77 69 62 55]
 [77 69 62 55]
 [75 67 63 48]
 [75 67 63 48]
 [75 69 63 48]
 [75 69 63 48]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [75 69 63 48]
 [75 69 63 48]
 [75 67 63 48]
 [75 67 63 48]
 [77 65 62 50]
 [77 65 62 50]
 [77 65 60 50]
 [77 65 60 50]
 [74 67 58 55]
 [74 67 58 55]
 [74 67 58 53]
 [74 67 58 53]
 [72 67 58 51]
 [72 67 58 51]
 [72 67 58 51]
 [72 67 58 51]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]
 [72 69 65 53]
 [72 

(260, 4)
tf.Tensor(
[[71 67 64 52]
 [71 67 64 52]
 [71 67 62 52]
 ...
 [64 59 56 52]
 [64 59 56 52]
 [64 59 56 52]], shape=(260, 4), dtype=int32)
(132, 4)
tf.Tensor(
[[67 62 59 55]
 [67 62 59 55]
 [67 62 59 54]
 [67 62 59 54]
 [67 64 59 52]
 [67 64 59 52]
 [67 64 59 50]
 [67 64 59 50]
 [69 64 57 48]
 [69 64 57 48]
 [69 62 54 50]
 [69 62 54 50]
 [71 62 55 43]
 [71 62 55 43]
 [71 64 55 43]
 [71 64 55 43]
 [69 66 57 50]
 [69 66 57 50]
 [71 66 57 50]
 [71 66 57 50]
 [72 64 57 45]
 [72 64 57 45]
 [71 67 62 47]
 [71 66 62 47]
 [69 64 60 48]
 [69 64 60 48]
 [69 66 59 50]
 [69 66 57 50]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [71 67 62 55]
 [71 67 62 55]
 [71 67 62 54]
 [71 67 62 54]
 [72 67 64 52]
 [72 67 64 52]
 [72 69 63 52]
 [72 69 63 52]
 [71 69 63 52]
 [71 69 63 52]
 [71 67 64 52]
 [71 67 64 52]
 [69 66 60 52]
 [69 66 60 52]
 [69 64 60 52]
 [69 63 60 52]
 [67 64 59 52]
 [67 64 59 52]
 [67 64 59 50]
 [67 64 59 50]
 [66 62 57 48]
 [66 62 57 48]
 [67 62 57 47]
 [67 62 5

(260, 4)
tf.Tensor(
[[71 64 55 52]
 [71 64 55 52]
 [71 64 55 52]
 ...
 [64 59 55 40]
 [64 59 55 40]
 [64 59 55 40]], shape=(260, 4), dtype=int32)
(292, 4)
tf.Tensor(
[[65 62 58 58]
 [65 62 58 58]
 [65 62 58 58]
 ...
 [70 65 62 46]
 [70 65 62 46]
 [70 65 62 46]], shape=(292, 4), dtype=int32)
(228, 4)
tf.Tensor(
[[70 65 62 58]
 [70 65 62 58]
 [70 65 62 58]
 [70 65 62 58]
 [70 67 63 51]
 [70 67 63 51]
 [72 69 63 51]
 [72 69 63 51]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 63 53]
 [72 69 63 53]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [69 67 63 48]
 [69 67 63 48]
 [69 67 63 48]
 [69 67 63 48]
 [69 66 62 50]
 [69 66 62 50]
 [69 66 60 50]
 [69 66 60 50]
 [67 67 58 51]
 [67 67 58 51]
 [67 67 58 51]
 [67 67 58 51]
 [74 67 58 55]
 [74 67 58 55]
 [74 67 58 55]
 [74 67 58 55]
 [75 67 58 48]
 [75 67 58 48]
 [75 67 58 48]
 [75 67 58 48]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 51]
 [72 65 57 51]
 [74 65 58 50]
 [74 65 58 50

(260, 4)
tf.Tensor(
[[74 69 66 62]
 [74 69 66 62]
 [74 69 64 61]
 ...
 [62 57 54 38]
 [62 57 54 38]
 [62 57 54 38]], shape=(260, 4), dtype=int32)
(272, 4)
tf.Tensor(
[[76 68 59 52]
 [76 68 59 52]
 [76 69 59 54]
 ...
 [64 59 56 52]
 [64 59 56 52]
 [64 59 56 52]], shape=(272, 4), dtype=int32)
(164, 4)
tf.Tensor(
[[67 62 59 43]
 [67 62 59 43]
 [67 62 57 45]
 [67 62 57 45]
 [67 62 55 47]
 [67 62 55 47]
 [67 62 55 48]
 [67 62 55 48]
 [62 57 54 50]
 [62 57 54 50]
 [62 57 54 48]
 [62 57 54 48]
 [67 62 55 47]
 [67 62 55 47]
 [67 62 55 47]
 [67 62 55 47]
 [72 69 55 45]
 [72 69 55 45]
 [72 69 54 45]
 [72 69 54 45]
 [71 62 55 43]
 [71 62 55 43]
 [71 62 55 47]
 [71 62 55 47]
 [69 62 55 50]
 [69 62 55 50]
 [69 62 54 50]
 [69 60 54 50]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 55 52]
 [67 59 55 52]
 [67 61 55 52]
 [67 61 55 52]
 [69 62 54 50]
 [69 62 54 50]
 [71 65 56 50]
 [71 65 56 50]
 [72 64 57 45]
 [72 64 57 45]
 [72 66 57 45]
 [72 66 57 45]
 [71 67 50 47]
 [71 67 50 47

In [13]:
print("TRAIN SET:", train_set)
print("")
for i in train_set.take(1):
    print("I:", i)
    print("")
    for j in i.take(1): 
        print("J:", j)
        for h in j:
            print("H:", h)

# additional loop is needed for the window function because it  
# Combines (nests of) input elements into a dataset of (nests of) windows.

TRAIN SET: <MapDataset shapes: DatasetSpec(DatasetSpec(TensorSpec(shape=(4,), dtype=tf.int32, name=None), TensorShape([])), TensorShape([])), types: DatasetSpec(DatasetSpec(TensorSpec(shape=(4,), dtype=tf.int32, name=None), TensorShape([])), TensorShape([]))>

I: <_VariantDataset shapes: DatasetSpec(TensorSpec(shape=(4,), dtype=tf.int32, name=None), TensorShape([])), types: DatasetSpec(TensorSpec(shape=(4,), dtype=tf.int32, name=None), TensorShape([]))>

J: <_VariantDataset shapes: (4,), types: tf.int32>
H: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
H: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
H: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
H: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
H: tf.Tensor([75 70 58 55], shape=(4,), dtype=int32)
H: tf.Tensor([75 70 58 55], shape=(4,), dtype=int32)
H: tf.Tensor([75 70 60 55], shape=(4,), dtype=int32)
H: tf.Tensor([75 70 60 55], shape=(4,), dtype=int32)
H: tf.Tensor([77 69 62 50], shape=(4,), dtype=int32)
H: tf.Tensor(

In [14]:
print("TRAIN SET:", train_set1)
print("")
for i in train_set1.take(1): # dataset for every chorale; total of 229 for train
    print("I:", i)
    for j in i: # every nested dataset has as many tensors as chords in that chorale
        print("J:", j)

TRAIN SET: <MapDataset shapes: DatasetSpec(TensorSpec(shape=(4,), dtype=tf.int32, name=None), TensorShape([])), types: DatasetSpec(TensorSpec(shape=(4,), dtype=tf.int32, name=None), TensorShape([]))>

I: <_VariantDataset shapes: (4,), types: tf.int32>
J: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
J: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
J: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
J: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
J: tf.Tensor([75 70 58 55], shape=(4,), dtype=int32)
J: tf.Tensor([75 70 58 55], shape=(4,), dtype=int32)
J: tf.Tensor([75 70 60 55], shape=(4,), dtype=int32)
J: tf.Tensor([75 70 60 55], shape=(4,), dtype=int32)
J: tf.Tensor([77 69 62 50], shape=(4,), dtype=int32)
J: tf.Tensor([77 69 62 50], shape=(4,), dtype=int32)
J: tf.Tensor([77 69 62 50], shape=(4,), dtype=int32)
J: tf.Tensor([77 69 62 50], shape=(4,), dtype=int32)
J: tf.Tensor([77 70 62 55], shape=(4,), dtype=int32)
J: tf.Tensor([77 70 62 55], shape=(4,), dtype=int32)
J: tf.

In [15]:
counter = 0
for _ in train_set1: # a dataset for every chorale
    counter += 1
counter

229

In [16]:
counter = 0
for i in train_set: # dataset for every chorale
    counter += 1
counter

229

In [17]:
counter = 0
for i in train_set.take(3): 
    for j in i: # the number of variant datasets within i 
        counter += 1
        print(j)
    print("")
counter

<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>

<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: t

40

In [18]:
counter = 0
c = 1
for i in train_set.take(2):
    if c == 1:
        c += 1
        continue
    for j in i.take(2): 
        for h in j:
            print(h)
            counter += 1
        print("")
counter

tf.Tensor([69 64 61 57], shape=(4,), dtype=int32)
tf.Tensor([69 64 61 57], shape=(4,), dtype=int32)
tf.Tensor([69 64 61 57], shape=(4,), dtype=int32)
tf.Tensor([69 64 61 57], shape=(4,), dtype=int32)
tf.Tensor([71 64 59 56], shape=(4,), dtype=int32)
tf.Tensor([71 64 59 56], shape=(4,), dtype=int32)
tf.Tensor([71 64 57 54], shape=(4,), dtype=int32)
tf.Tensor([71 64 57 54], shape=(4,), dtype=int32)
tf.Tensor([71 64 56 52], shape=(4,), dtype=int32)
tf.Tensor([71 64 56 52], shape=(4,), dtype=int32)
tf.Tensor([71 64 56 50], shape=(4,), dtype=int32)
tf.Tensor([71 64 56 50], shape=(4,), dtype=int32)
tf.Tensor([69 64 57 49], shape=(4,), dtype=int32)
tf.Tensor([69 64 57 49], shape=(4,), dtype=int32)
tf.Tensor([69 64 57 49], shape=(4,), dtype=int32)
tf.Tensor([69 64 57 49], shape=(4,), dtype=int32)
tf.Tensor([66 62 57 50], shape=(4,), dtype=int32)
tf.Tensor([66 62 57 50], shape=(4,), dtype=int32)
tf.Tensor([66 61 57 50], shape=(4,), dtype=int32)
tf.Tensor([66 61 57 50], shape=(4,), dtype=int32)


66

In [19]:
counter = 0
for i in train_set2.take(1):
    for j in i: 
        print(j)
    print("")
counter

<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>
<_VariantDataset shapes: (4,), types: tf.int32>



0

In [20]:
for i in train_set2.take(1):
    print("I:", i)
    for j in i.take(1):
        print("J:", j)
        for h in j:
            print("H:", h)

I: <_VariantDataset shapes: DatasetSpec(TensorSpec(shape=(4,), dtype=tf.int32, name=None), TensorShape([])), types: DatasetSpec(TensorSpec(shape=(4,), dtype=tf.int32, name=None), TensorShape([]))>
J: <_VariantDataset shapes: (4,), types: tf.int32>
H: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
H: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
H: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
H: tf.Tensor([74 70 65 58], shape=(4,), dtype=int32)
H: tf.Tensor([75 70 58 55], shape=(4,), dtype=int32)
H: tf.Tensor([75 70 58 55], shape=(4,), dtype=int32)
H: tf.Tensor([75 70 60 55], shape=(4,), dtype=int32)
H: tf.Tensor([75 70 60 55], shape=(4,), dtype=int32)
H: tf.Tensor([77 69 62 50], shape=(4,), dtype=int32)
H: tf.Tensor([77 69 62 50], shape=(4,), dtype=int32)
H: tf.Tensor([77 69 62 50], shape=(4,), dtype=int32)
H: tf.Tensor([77 69 62 50], shape=(4,), dtype=int32)
H: tf.Tensor([77 70 62 55], shape=(4,), dtype=int32)
H: tf.Tensor([77 70 62 55], shape=(4,), dtype=int32)
H: tf.Tens

In [21]:
counter = 0
counter1 = 0
for i in train_set3.take(1):
    counter += 1
    print("I:", i)
    for j in i:
        print("J:", j)
        print("")
#         for h in j:
#             print("H:", h)
counter # 229

I: <_VariantDataset shapes: (None, 4), types: tf.int32>
J: tf.Tensor(
[[74 70 65 58]
 [74 70 65 58]
 [74 70 65 58]
 [74 70 65 58]
 [75 70 58 55]
 [75 70 58 55]
 [75 70 60 55]
 [75 70 60 55]
 [77 69 62 50]
 [77 69 62 50]
 [77 69 62 50]
 [77 69 62 50]
 [77 70 62 55]
 [77 70 62 55]
 [77 69 62 55]
 [77 69 62 55]
 [75 67 63 48]
 [75 67 63 48]
 [75 69 63 48]
 [75 69 63 48]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [74 70 65 46]], shape=(33, 4), dtype=int32)

J: tf.Tensor(
[[75 67 63 48]
 [75 67 63 48]
 [75 69 63 48]
 [75 69 63 48]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [75 69 63 48]
 [75 69 63 48]
 [75 67 63 48]
 [75 67 63 48]
 [77 65 62 50]
 [77 65 62 50]


1

In [22]:
counter = 0
for i in train_set4:
    counter += 1
    print("I:", i)
#     for j in i:
#         print("J:", j); print("")
counter

I: tf.Tensor(
[[74 70 65 58]
 [74 70 65 58]
 [74 70 65 58]
 [74 70 65 58]
 [75 70 58 55]
 [75 70 58 55]
 [75 70 60 55]
 [75 70 60 55]
 [77 69 62 50]
 [77 69 62 50]
 [77 69 62 50]
 [77 69 62 50]
 [77 70 62 55]
 [77 70 62 55]
 [77 69 62 55]
 [77 69 62 55]
 [75 67 63 48]
 [75 67 63 48]
 [75 69 63 48]
 [75 69 63 48]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [74 70 65 46]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[75 67 63 48]
 [75 67 63 48]
 [75 69 63 48]
 [75 69 63 48]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [72 69 65 53]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [74 70 65 46]
 [75 69 63 48]
 [75 69 63 48]
 [75 67 63 48]
 [75 67 63 48]
 [77 65 62 50]
 [77 65 62 50]
 [77 65 60 50]
 [77 65 60 50]
 [74 67 58 55]
 [74 67 58 5

 [76 67 60 60]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[72 65 60 57]
 [72 65 60 57]
 [72 65 60 57]
 [72 65 60 57]
 [74 62 59 59]
 [74 62 59 59]
 [74 62 59 59]
 [74 62 59 59]
 [74 67 59 55]
 [74 67 59 55]
 [74 67 59 55]
 [74 67 59 55]
 [76 67 60 60]
 [76 67 60 60]
 [76 67 60 60]
 [76 67 60 60]
 [76 67 60 60]
 [76 67 60 60]
 [76 67 60 60]
 [76 67 60 60]
 [76 67 58 48]
 [76 67 58 48]
 [76 67 58 48]
 [76 67 58 48]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[76 67 60 60]
 [76 67 60 60]
 [76 67 60 60]
 [76 67 60 60]
 [76 67 58 48]
 [76 67 58 48]
 [76 67 58 48]
 [76 67 58 48]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [72 65 57 53]
 [76 67 60 48]
 [76 67 60 48]
 [76 67 60 48]
 [76 67 60 48]
 [76 67 60 48]
 [76 67 60 48]
 [76 67 60 4

I: tf.Tensor(
[[63 62 55 48]
 [63 62 55 48]
 [63 60 55 48]
 [63 62 55 48]
 [67 63 60 48]
 [67 63 60 48]
 [67 63 58 48]
 [67 63 58 48]
 [69 63 57 42]
 [69 63 57 42]
 [69 62 57 42]
 [69 62 57 42]
 [70 62 55 43]
 [70 62 55 43]
 [70 62 55 43]
 [70 62 55 43]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [68 67 63 48]
 [68 67 63 48]
 [68 65 58 50]
 [68 65 58 50]
 [67 65 58 51]
 [67 65 58 51]
 [67 63 58 51]
 [67 63 58 51]
 [65 63 60 45]
 [65 63 60 45]
 [65 62 55 47]
 [65 62 55 47]
 [63 60 55 48]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [68 67 63 48]
 [68 67 63 48]
 [68 65 58 50]
 [68 65 58 50]
 [67 65 58 51]
 [67 65 58 51]
 [67 63 58 51]
 [67 63 58 51]
 [65 63 60 45]
 [65 63 60 45]
 [65 62 55 47]
 [65 62 55 47]
 [63 60 55 48]
 [63 60 55 48]
 [65 62 55 48]
 [65 62 55 48]
 [67 63 60 48]
 [67 63 60 48]
 [67 63 58 48]
 [67 63 58 48]
 [69 63 60 41]
 [69 63 60 41]
 [69 63 60 41]
 [69 63 60 41]
 [70 62 58 46]
 [70 62 58 4

 [76 69 57 49]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[74 69 62 53]
 [74 69 62 53]
 [74 69 62 53]
 [74 69 62 53]
 [74 69 62 58]
 [74 69 62 58]
 [74 67 64 58]
 [74 67 64 58]
 [74 71 65 57]
 [74 71 65 57]
 [74 71 65 56]
 [74 71 65 56]
 [73 69 64 57]
 [73 69 64 57]
 [73 69 64 57]
 [73 69 64 57]
 [76 69 57 49]
 [76 69 57 49]
 [76 67 57 49]
 [76 67 57 49]
 [74 65 57 50]
 [74 65 57 50]
 [74 65 57 52]
 [74 65 57 52]
 [69 65 62 53]
 [69 65 62 53]
 [69 65 62 53]
 [69 65 62 53]
 [70 67 62 53]
 [70 67 62 53]
 [70 67 60 52]
 [70 67 60 52]
 [69 65 60 53]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[76 69 57 49]
 [76 69 57 49]
 [76 67 57 49]
 [76 67 57 49]
 [74 65 57 50]
 [74 65 57 50]
 [74 65 57 52]
 [74 65 57 52]
 [69 65 62 53]
 [69 65 62 53]
 [69 65 62 53]
 [69 65 62 53]
 [70 67 62 53]
 [70 67 62 53]
 [70 67 60 52]
 [70 67 60 52]
 [69 65 60 53]
 [69 65 60 53]
 [67 65 60 53]
 [67 65 60 53]
 [67 65 62 46]
 [67 65 62 46]
 [67 64 58 46]
 [67 62 58 46]
 [67 64 55 48]
 [67 64 55 48]
 [67 64 60 4

I: tf.Tensor(
[[71 66 59 51]
 [71 66 59 51]
 [69 66 59 51]
 [69 66 59 51]
 [67 66 59 52]
 [67 66 59 52]
 [67 64 60 52]
 [67 64 60 52]
 [69 64 60 54]
 [69 64 60 54]
 [69 63 59 54]
 [69 61 57 54]
 [71 59 59 55]
 [71 59 59 55]
 [69 63 59 54]
 [69 63 59 54]
 [67 64 59 55]
 [67 64 59 55]
 [67 64 59 57]
 [67 64 59 57]
 [66 64 59 59]
 [66 64 59 59]
 [64 63 59 59]
 [64 61 59 59]
 [66 63 59 47]
 [66 63 59 47]
 [66 63 57 47]
 [66 63 57 47]
 [64 59 55 52]
 [64 59 55 52]
 [64 59 55 52]
 [64 59 55 52]
 [71 67 64 52]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[67 64 59 55]
 [67 64 59 55]
 [67 64 59 57]
 [67 64 59 57]
 [66 64 59 59]
 [66 64 59 59]
 [64 63 59 59]
 [64 61 59 59]
 [66 63 59 47]
 [66 63 59 47]
 [66 63 57 47]
 [66 63 57 47]
 [64 59 55 52]
 [64 59 55 52]
 [64 59 55 52]
 [64 59 55 52]
 [71 67 64 52]
 [71 67 64 52]
 [71 67 62 52]
 [71 67 62 52]
 [70 66 61 52]
 [70 66 61 52]
 [70 66 61 52]
 [70 66 61 52]
 [71 66 62 50]
 [71 66 62 50]
 [73 70 64 49]
 [73 70 64 49]
 [74 71 66 47]
 [74 71 66 4

...

I: tf.Tensor(
[[71 67 64 52]
 [71 67 64 52]
 [71 66 64 54]
 [71 66 64 54]
 [71 64 59 55]
 [71 64 59 55]
 [71 63 59 55]
 [71 63 59 55]
 [72 64 57 48]
 [72 64 57 48]
 [72 66 57 50]
 [72 66 57 50]
 [71 67 55 52]
 [71 67 55 52]
 [71 67 55 52]
 [71 67 55 52]
 [69 67 64 49]
 [69 67 64 49]
 [69 67 64 49]
 [69 67 64 49]
 [69 66 62 50]
 [69 66 62 50]
 [67 66 62 50]
 [67 66 62 50]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [71 67 62 55]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[69 67 64 49]
 [69 67 64 49]
 [69 67 64 49]
 [69 67 64 49]
 [69 66 62 50]
 [69 66 62 50]
 [67 66 62 50]
 [67 66 62 50]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [67 62 59 43]
 [71 67 62 55]
 [71 67 62 55]
 [71 67 62 54]
 [71 67 62 54]
 [73 67 64 52]
 [73 67 64 52]
 [73 67 64 52]
 [73 67 64 52]
 [74 66 58 54]
 [74 66 58 54]
 [74 66 58 52]
 [74 66 58 52]
 [71 66 59 50]
 [71 66 59 5

I: tf.Tensor(
[[66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [71 62 55 55]
 [71 62 55 55]
 [71 62 55 55]
 [71 62 55 55]
 [69 62 57 54]
 [69 62 57 54]
 [69 62 57 54]
 [69 62 57 54]
 [67 62 59 47]
 [67 62 59 47]
 [67 64 57 49]
 [67 64 57 49]
 [66 64 57 50]
 [66 64 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [64 62 59 43]
 [64 62 59 43]
 [64 62 59 43]
 [64 62 59 43]
 [64 61 57 45]
 [64 61 57 45]
 [64 61 57 45]
 [64 61 57 45]
 [66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [73 64 58 49]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[66 64 57 50]
 [66 64 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [64 62 59 43]
 [64 62 59 43]
 [64 62 59 43]
 [64 62 59 43]
 [64 61 57 45]
 [64 61 57 45]
 [64 61 57 45]
 [64 61 57 45]
 [66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [73 64 58 49]
 [73 64 58 49]
 [73 64 58 49]
 [73 64 58 49]
 [74 62 59 47]
 [74 62 59 47]
 [74 64 59 49]
 [74 64 59 49]
 [74 66 59 50]
 [74 66 59 50]
 [74 66 59 52]
 [74 66 59 52]
 [73 66 59 54]
 [73 66 59 5

I: tf.Tensor(
[[69 62 54 50]
 [69 62 54 50]
 [69 60 54 50]
 [69 60 54 50]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [67 59 50 43]
 [71 67 62 43]
 [71 67 62 43]
 [71 67 62 43]
 [71 67 62 43]
 [69 66 62 50]
 [69 66 62 50]
 [69 66 60 50]
 [69 66 60 50]
 [71 66 59 51]
 [71 66 59 51]
 [71 66 59 51]
 [71 66 59 51]
 [67 64 59 52]
 [67 64 59 52]
 [67 62 59 52]
 [67 62 59 52]
 [64 61 57 57]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[71 67 62 43]
 [71 67 62 43]
 [71 67 62 43]
 [71 67 62 43]
 [69 66 62 50]
 [69 66 62 50]
 [69 66 60 50]
 [69 66 60 50]
 [71 66 59 51]
 [71 66 59 51]
 [71 66 59 51]
 [71 66 59 51]
 [67 64 59 52]
 [67 64 59 52]
 [67 62 59 52]
 [67 62 59 52]
 [64 61 57 57]
 [64 61 57 57]
 [64 61 57 55]
 [64 61 57 55]
 [66 62 57 54]
 [66 62 57 54]
 [66 62 57 54]
 [66 62 57 54]
 [67 62 55 52]
 [67 62 55 52]
 [67 61 55 52]
 [67 61 55 52]
 [69 62 54 50]
 [69 62 54 5

I: tf.Tensor(
[[63 60 53 45]
 [63 60 53 45]
 [63 60 53 45]
 [63 60 53 45]
 [62 58 53 46]
 [62 58 53 46]
 [62 58 53 46]
 [62 58 53 46]
 [67 58 55 51]
 [67 58 55 51]
 [67 60 57 51]
 [67 60 57 51]
 [67 62 58 50]
 [67 62 58 50]
 [67 62 58 50]
 [67 62 58 50]
 [66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [69 66 62 50]], shape=(33, 4), dtype=int32)
I: tf.Tensor(
[[66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [66 62 57 50]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [67 62 58 43]
 [69 66 62 50]
 [69 66 62 50]
 [69 66 62 50]
 [69 66 62 50]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [70 67 62 55]
 [72 65 60 57]
 [72 65 60 57]
 [72 65 60 57]
 [72 65 60 57]
 [74 65 58 58]
 [74 65 58 5

3111

In [23]:
for i in train_set5:
    print("I:", i)

I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[39, 35, 30, ..., 39, 35, 30],
       [40, 32, 28, ..., 37, 32, 23],
       [39, 35, 30, ..., 37, 34, 30],
       ...,
       [32, 27, 24, ..., 37, 29, 20],
       [34, 27, 19, ..., 39, 31, 27],
       [37, 29, 20, ..., 36, 32, 20]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[35, 30, 23, ..., 35, 30, 11],
       [32, 28, 13, ..., 32, 23, 16],
       [35, 30, 11, ..., 34, 30, 18],
       ...,
       [27, 24,  8, ..., 29, 20, 20],
       [27, 19, 15, ..., 31, 27, 24],
       [29, 20, 20, ..., 32, 20, 17]])>)
I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[39, 31, 27, ..., 39, 32, 24],
       [36, 32, 20, ..., 34, 31, 27],
       [37, 32, 29, ..., 36, 32, 27],
       ...,
       [36, 29, 24, ..., 29, 25, 22],
       [36, 33, 29, ..., 29, 29, 24],
       [29, 25, 22, ..., 36, 29, 24]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[31, 27, 24, ..., 32, 24, 20],
       [32, 20, 17, ..., 31, 

I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[34, 31, 27, ..., 32, 22, 20],
       [32, 27, 23, ..., 34, 31, 27],
       [32, 22, 20, ..., 38, 32, 22],
       ...,
       [35, 32, 27, ..., 35, 20, 27],
       [34, 32, 28, ..., 35, 27, 22],
       [35, 20, 27, ..., 32, 24, 15]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[31, 27, 15, ..., 22, 20,  4],
       [27, 23,  8, ..., 31, 27, 15],
       [22, 20,  4, ..., 32, 22, 10],
       ...,
       [32, 27, 20, ..., 20, 27,  8],
       [32, 28, 10, ..., 27, 22,  8],
       [20, 27,  8, ..., 24, 15,  8]])>)
I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[39, 32, 24, ..., 34, 34, 27],
       [39, 31, 22, ..., 37, 32, 29],
       [34, 34, 27, ..., 39, 32, 24],
       ...,
       [35, 27, 23, ..., 34, 30, 25],
       [32, 27, 24, ..., 36, 32, 27],
       [36, 32, 27, ..., 34, 31, 27]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[32, 24, 20, ..., 34, 27, 19],
       [31, 22, 19, ..., 32, 

I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[32, 24, 20, ..., 27, 27, 19],
       [32, 27, 24, ..., 31, 28, 24],
       [27, 27, 19, ..., 36, 32, 27],
       ...,
       [29, 24, 21, ..., 34, 29, 26],
       [38, 29, 24, ..., 34, 29, 26],
       [34, 29, 26, ..., 34, 29, 26]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[24, 20, 17, ..., 27, 19, 12],
       [27, 24, 20, ..., 28, 24, 12],
       [27, 19, 12, ..., 32, 27,  8],
       ...,
       [24, 21, 17, ..., 29, 26, 22],
       [29, 24, 22, ..., 29, 26, 22],
       [29, 26, 22, ..., 29, 26, 26]])>)
I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[34, 29, 26, ..., 29, 24, 21],
       [34, 29, 26, ..., 38, 29, 24],
       [29, 24, 21, ..., 34, 29, 26],
       ...,
       [29, 24, 20, ..., 36, 32, 27],
       [29, 29, 25, ..., 43, 31, 26],
       [36, 32, 27, ..., 38, 29, 20]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[29, 26, 22, ..., 24, 21, 17],
       [29, 26, 26, ..., 29, 

I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[39, 34, 31, ..., 39, 32, 30],
       [39, 34, 31, ..., 34, 31, 27],
       [39, 32, 30, ..., 34, 31, 25],
       ...,
       [36, 36, 27, ..., 34, 31, 27],
       [39, 31, 24, ..., 39, 29, 24],
       [34, 31, 27, ..., 34, 31, 22]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[34, 31, 22, ..., 32, 30, 13],
       [34, 31, 27, ..., 31, 27, 15],
       [32, 30, 13, ..., 31, 25, 15],
       ...,
       [36, 27, 20, ..., 31, 27, 15],
       [31, 24, 24, ..., 29, 24,  9],
       [31, 27, 15, ..., 31, 22, 15]])>)
I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[39, 29, 24, ..., 32, 27, 24],
       [39, 34, 31, ..., 39, 36, 19],
       [38, 29, 32, ..., 36, 27, 24],
       ...,
       [37, 32, 25, ..., 27, 22, 18],
       [29, 27, 22, ..., 32, 30, 25],
       [32, 27, 24, ..., 32, 24, 20]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[29, 24,  9, ..., 27, 24,  8],
       [34, 31, 27, ..., 36, 

I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[36, 31, 24, ..., 29, 24, 20],
       [34, 29, 24, ..., 29, 25, 22],
       [29, 24, 20, ..., 36, 27, 24],
       ...,
       [37, 31, 28, ..., 39, 31, 22],
       [37, 32, 28, ..., 37, 31, 27],
       [39, 31, 22, ..., 34, 31, 27]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[31, 24, 16, ..., 24, 20, 17],
       [29, 24, 17, ..., 25, 22, 13],
       [24, 20, 17, ..., 27, 24, 20],
       ...,
       [31, 28,  8, ..., 31, 22, 15],
       [32, 28, 13, ..., 31, 27, 15],
       [31, 22, 15, ..., 31, 27, 15]])>)
I: (<tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[37, 31, 27, ..., 35, 32, 27],
       [34, 31, 27, ..., 35, 32, 28],
       [35, 32, 27, ..., 39, 35, 30],
       ...,
       [36, 32, 27, ..., 36, 32, 27],
       [36, 32, 27, ..., 34, 29, 25],
       [36, 32, 27, ..., 32, 29, 24]])>, <tf.Tensor: shape=(32, 131), dtype=int32, numpy=
array([[31, 27, 15, ..., 32, 27,  8],
       [31, 27, 15, ..., 32, 

In [24]:
def create_target(batch):
    X = batch[:, :-1]
    Y = batch[:, 1:] # predict next note in each arpegio, at each step
    return X, Y

def preprocess(window):
    window = tf.where(window == 0, window, window - min_note + 1) # shift values
    return tf.reshape(window, [-1]) # convert to arpegio

def bach_dataset(chorales, batch_size=32, shuffle_buffer_size=None,
                 window_size=32, window_shift=16, cache=True):
    def batch_window(window):
        return window.batch(window_size + 1)

    def to_windows(chorale):
        dataset = tf.data.Dataset.from_tensor_slices(chorale)
        dataset = dataset.window(window_size + 1, window_shift, drop_remainder=True)
        return dataset.flat_map(batch_window)

    chorales = tf.ragged.constant(chorales, ragged_rank=1)
    dataset = tf.data.Dataset.from_tensor_slices(chorales)
    dataset = dataset.flat_map(to_windows).map(preprocess)
    if cache:
        dataset = dataset.cache()
    if shuffle_buffer_size:
        dataset = dataset.shuffle(shuffle_buffer_size)
    dataset = dataset.batch(batch_size)
    dataset = dataset.map(create_target)
    return dataset.prefetch(1)

train_set = bach_dataset(train_chorales, shuffle_buffer_size=1000)
valid_set = bach_dataset(valid_chorales)
test_set = bach_dataset(test_chorales)

### Creating and Compiling the Model

In [25]:
# embedding_test = keras.layers.Embedding(input_dim=n_notes, output_dim=n_embedding_dims,
#                            input_shape=[None])

# this works because normally, you would use a TextVectorization layer that would
# create a table init, a vocab table with oov buckets, and lookup the inputs
# however since the inputs are already shifted, you can skip this step

In [28]:
n_notes = 47
n_embedding_dims = 5
model = keras.models.Sequential([])
model.add(keras.layers.Embedding(input_dim=n_notes, output_dim=n_embedding_dims,
                            input_shape=[None]))
for rate in (1, 2, 4, 8) * 2:
    model.add(keras.layers.Conv1D(20, 2, padding="causal", activation="relu", dilation_rate=rate))
    model.add(keras.layers.BatchNormalization())
model.add(keras.layers.LSTM(64, return_sequences=True))
model.add(keras.layers.GRU(128, return_sequences=True))
model.add(keras.layers.SimpleRNN(256, return_sequences=True))
model.add(keras.layers.Dense(n_notes, activation="softmax"))

model.compile(loss="sparse_categorical_crossentropy", optimizer="adam", metrics=["accuracy"])

In [30]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_1 (Embedding)      (None, None, 5)           235       
_________________________________________________________________
conv1d (Conv1D)              (None, None, 20)          220       
_________________________________________________________________
batch_normalization (BatchNo (None, None, 20)          80        
_________________________________________________________________
conv1d_1 (Conv1D)            (None, None, 20)          820       
_________________________________________________________________
batch_normalization_1 (Batch (None, None, 20)          80        
_________________________________________________________________
conv1d_2 (Conv1D)            (None, None, 20)          820       
_________________________________________________________________
batch_normalization_2 (Batch (None, None, 20)         

### Training

In [29]:
model.fit(train_set, epochs=20, validation_data=valid_set)

Epoch 1/20
98/98 [==============================] - 24s 181ms/step - loss: 3.3107 - accuracy: 0.1141 - val_loss: 3.9120 - val_accuracy: 0.0855
Epoch 2/20
98/98 [==============================] - 16s 167ms/step - loss: 2.0910 - accuracy: 0.3511 - val_loss: 3.6121 - val_accuracy: 0.1304
Epoch 3/20
98/98 [==============================] - 17s 169ms/step - loss: 1.7591 - accuracy: 0.4607 - val_loss: 3.5334 - val_accuracy: 0.1243
Epoch 4/20
98/98 [==============================] - 16s 162ms/step - loss: 1.5531 - accuracy: 0.5368 - val_loss: 3.1110 - val_accuracy: 0.1481
Epoch 5/20
98/98 [==============================] - 16s 163ms/step - loss: 1.3731 - accuracy: 0.6011 - val_loss: 2.4676 - val_accuracy: 0.3034
Epoch 6/20
98/98 [==============================] - 16s 159ms/step - loss: 1.2595 - accuracy: 0.6390 - val_loss: 1.9102 - val_accuracy: 0.4227
Epoch 7/20
98/98 [==============================] - 17s 174ms/step - loss: 1.1669 - accuracy: 0.6670 - val_loss: 1.2956 - val_accuracy: 0.6286

+ evaluation is simply listening to the music however you can also evaluate it on the test set or use it for the train set

### Predictions

In [54]:
seed_chords = test_chorales[2][:8] # 2D matrix of chords: chords x 4
for i in seed_chords:
    print(i)

[73, 68, 61, 53]
[73, 68, 61, 53]
[73, 68, 61, 53]
[73, 68, 61, 53]
[69, 66, 61, 54]
[69, 66, 61, 54]
[69, 66, 61, 54]
[69, 66, 61, 54]


In [55]:
arpegio = preprocess(tf.constant(seed_chords, dtype=tf.int64))
for i in arpegio:
    print(i)

tf.Tensor(38, shape=(), dtype=int64)
tf.Tensor(33, shape=(), dtype=int64)
tf.Tensor(26, shape=(), dtype=int64)
tf.Tensor(18, shape=(), dtype=int64)
tf.Tensor(38, shape=(), dtype=int64)
tf.Tensor(33, shape=(), dtype=int64)
tf.Tensor(26, shape=(), dtype=int64)
tf.Tensor(18, shape=(), dtype=int64)
tf.Tensor(38, shape=(), dtype=int64)
tf.Tensor(33, shape=(), dtype=int64)
tf.Tensor(26, shape=(), dtype=int64)
tf.Tensor(18, shape=(), dtype=int64)
tf.Tensor(38, shape=(), dtype=int64)
tf.Tensor(33, shape=(), dtype=int64)
tf.Tensor(26, shape=(), dtype=int64)
tf.Tensor(18, shape=(), dtype=int64)
tf.Tensor(34, shape=(), dtype=int64)
tf.Tensor(31, shape=(), dtype=int64)
tf.Tensor(26, shape=(), dtype=int64)
tf.Tensor(19, shape=(), dtype=int64)
tf.Tensor(34, shape=(), dtype=int64)
tf.Tensor(31, shape=(), dtype=int64)
tf.Tensor(26, shape=(), dtype=int64)
tf.Tensor(19, shape=(), dtype=int64)
tf.Tensor(34, shape=(), dtype=int64)
tf.Tensor(31, shape=(), dtype=int64)
tf.Tensor(26, shape=(), dtype=int64)
t

In [56]:
arpegio = tf.reshape(arpegio, [1, -1])
print(arpegio)
for i in arpegio:
    print(i)

tf.Tensor(
[[38 33 26 18 38 33 26 18 38 33 26 18 38 33 26 18 34 31 26 19 34 31 26 19
  34 31 26 19 34 31 26 19]], shape=(1, 32), dtype=int64)
tf.Tensor(
[38 33 26 18 38 33 26 18 38 33 26 18 38 33 26 18 34 31 26 19 34 31 26 19
 34 31 26 19 34 31 26 19], shape=(32,), dtype=int64)


In [41]:
for note in range(4): # generates class probabilities for each of the 47 notes for 1 chord
    next_note = model.predict(arpegio)
    print(next_note)

[[[2.46118940e-03 1.67908322e-04 1.14823655e-04 ... 6.96580828e-05
   1.09153545e-04 3.44916079e-05]
  [7.96695182e-04 2.25912063e-05 5.70583188e-06 ... 8.38719302e-07
   9.46141790e-06 4.58621003e-07]
  [3.85306303e-05 1.54159043e-05 1.21511130e-05 ... 2.13402996e-06
   1.50537323e-06 2.48390620e-06]
  ...
  [1.15317935e-05 1.81527859e-09 5.29005710e-08 ... 1.48438462e-09
   1.48173198e-08 2.35920750e-09]
  [2.76640577e-07 2.42431009e-09 1.26576452e-07 ... 5.32182964e-09
   1.26130049e-08 1.06194172e-07]
  [7.30398824e-05 6.31753096e-07 1.24435155e-05 ... 2.44092706e-04
   1.30656399e-05 1.02575541e-04]]]
[[[2.46118940e-03 1.67908322e-04 1.14823655e-04 ... 6.96580828e-05
   1.09153545e-04 3.44916079e-05]
  [7.96695182e-04 2.25912063e-05 5.70583188e-06 ... 8.38719302e-07
   9.46141790e-06 4.58621003e-07]
  [3.85306303e-05 1.54159043e-05 1.21511130e-05 ... 2.13402996e-06
   1.50537323e-06 2.48390620e-06]
  ...
  [1.15317935e-05 1.81527859e-09 5.29005710e-08 ... 1.48438462e-09
   1.48173

In [43]:
next_note.shape

(1, 32, 47)

In [46]:
np.argmax(next_note, axis=-1), np.argmax(next_note, axis=-1).shape

(array([[34, 29, 17, 38, 33, 26, 18, 38, 33, 26, 18, 38, 33, 26, 18, 38,
         31, 26, 19, 34, 31, 26, 19, 34, 31, 26, 19, 34, 31, 26, 19, 36]],
       dtype=int64),
 (1, 32))

In [52]:
for note in range(4): # generates class probabilities for each of the 47 notes for 1 chord
    next_note = np.argmax(model.predict(arpegio), axis=-1)[:1, -1:] # take the first batch and the last value
    # remember the model will generate a prediction for every note/key in the arpegio, you just want the last one
    
print(next_note)

[[34 29 17 38 33 26 18 38 33 26 18 38 33 26 18 38 31 26 19 34 31 26 19 34
  31 26 19 34 31 26 19 36]]


In [53]:
for note in range(4):
        next_note = np.argmax(model.predict(arpegio), axis=-1)[:1, -1:]
        arpegio = tf.concat([arpegio, next_note], axis=1)
        
print(arpegio)

tf.Tensor(
[[38 33 26 18 38 33 26 18 38 33 26 18 38 33 26 18 34 31 26 19 34 31 26 19
  34 31 26 19 34 31 26 19 36 31 24 21]], shape=(1, 36), dtype=int64)


In [58]:
def generate_chorale(model, seed_chords, length):
    arpegio = preprocess(tf.constant(seed_chords, dtype=tf.int64))
    arpegio = tf.reshape(arpegio, [1, -1])
    for chord in range(length):
        for note in range(4):
            #next_note = model.predict_classes(arpegio)[:1, -1:]
            next_note = np.argmax(model.predict(arpegio), axis=-1)[:1, -1:]
            arpegio = tf.concat([arpegio, next_note], axis=1)
    arpegio = tf.where(arpegio == 0, arpegio, arpegio + min_note - 1)
    return tf.reshape(arpegio, shape=[-1, 4])

new_chorale = generate_chorale(model, seed_chords, 56)

+ it might be too conservative, so add some probabilities (any way you see fit) to spice it up